In [1]:
library(ArchR)
library(Seurat)
library(dplyr)
library(tidyr)
library(parallel)
library(BSgenome.Mmusculus.UCSC.mm10)
library(ChIPseeker)
library(TxDb.Mmusculus.UCSC.mm10.knownGene)
library(WebGestaltR)


                                                   / |
                                                 /    \
            .                                  /      |.
            \\\                              /        |.
              \\\                          /           `|.
                \\\                      /              |.
                  \                    /                |\
                  \\#####\           /                  ||
                ==###########>      /                   ||
                 \\##==......\    /                     ||
            ______ =       =|__ /__                     ||      \\\
        ,--' ,----`-,__ ___/'  --,-`-===================##========>
       \               '        ##_______ _____ ,--,__,=##,__   ///
        ,    __==    ___,-,__,--'#'  ==='      `-'    | ##,-/
        -,____,---'       \\####\\________________,--\\_##,/
           ___      .______        ______  __    __  .______      
          /   \     |   _ 

In [2]:
projdir <- '/nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis'

addArchRGenome("mm10")
addArchRThreads(threads = 45) 

MuSC_projAging1 <- readRDS(file.path(projdir, "MuSC_subset", "all_MuSCs", "Save-ArchR-Project.rds"))

Setting default genome to Mm10.

Setting default number of Parallel threads to 45.



In [18]:
source(file.path(projdir, 'ArchR_utilities.R'))
source("/nas/homes/benyang/HiC/13_MultiOme/custom_addPeak2GeneLinks.R")

Loading required package: GenomicInteractions

Loading required package: InteractionSet



In [4]:
MuSC_projAging1


           ___      .______        ______  __    __  .______      
          /   \     |   _  \      /      ||  |  |  | |   _  \     
         /  ^  \    |  |_)  |    |  ,----'|  |__|  | |  |_)  |    
        /  /_\  \   |      /     |  |     |   __   | |      /     
       /  _____  \  |  |\  \\___ |  `----.|  |  |  | |  |\  \\___.
      /__/     \__\ | _| `._____| \______||__|  |__| | _| `._____|
    



class: ArchRProject 
outputDirectory: /nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/output 
samples(4): Aged_v2 Young_v2 Aged Young
sampleColData names(1): ArrowFiles
cellColData names(32): Sample TSSEnrichment ... ReadsInPeaks FRIP
numberOfCells(1): 997
medianTSS(1): 25.601
medianFrags(1): 5221

# MuSC dimension reduction 

In [5]:
MuSC_projAging1 <- addIterativeLSI(
    ArchRProj = MuSC_projAging1,
    useMatrix = "TileMatrix", 
    name = "IterativeLSI", 
    iterations = 2, 
    clusterParams = list( #See Seurat::FindClusters
        resolution = c(0.2), 
        sampleCells = 10000, 
        n.start = 10
    ), 
    varFeatures = 25000, 
    dimsToUse = 1:30,
    force=TRUE
)

Checking Inputs...

ArchR logging to : ArchRLogs/ArchR-addIterativeLSI-718d3d4f0642-Date-2022-12-23_Time-17-04-21.log
If there is an issue, please report to github with logFile!

2022-12-23 17:04:24 : Computing Total Across All Features, 0.04 mins elapsed.

2022-12-23 17:04:32 : Computing Top Features, 0.173 mins elapsed.

###########
2022-12-23 17:04:34 : Running LSI (1 of 2) on Top Features, 0.197 mins elapsed.
###########

2022-12-23 17:04:34 : Creating Partial Matrix, 0.198 mins elapsed.

2022-12-23 17:04:37 : Computing LSI, 0.261 mins elapsed.

2022-12-23 17:04:48 : Identifying Clusters, 0.432 mins elapsed.

2022-12-23 17:04:49 : Identified 3 Clusters, 0.46 mins elapsed.

2022-12-23 17:04:49 : Saving LSI Iteration, 0.461 mins elapsed.

2022-12-23 17:05:00 : Creating Cluster Matrix on the total Group Features, 0.63 mins elapsed.

2022-12-23 17:05:07 : Computing Variable Features, 0.755 mins elapsed.

###########
2022-12-23 17:05:07 : Running LSI (2 of 2) on Variable Features, 0.757

In [6]:
MuSC_projAging1 <- addUMAP(
    ArchRProj = MuSC_projAging1, 
    reducedDims = "IterativeLSI", 
    name = "UMAP", 
    nNeighbors = 30, 
    minDist = 0.5, 
    metric = "cosine",
    force = TRUE
)

Filtering 1 dims correlated > 0.75 to log10(depth + 1)

17:05:22 UMAP embedding parameters a = 0.583 b = 1.334

17:05:22 Read 997 rows and found 29 numeric columns

17:05:22 Using Annoy for neighbor search, n_neighbors = 30

17:05:22 Building Annoy index with metric = cosine, n_trees = 50

0%   10   20   30   40   50   60   70   80   90   100%

[----|----|----|----|----|----|----|----|----|----|

*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
|

17:05:22 Writing NN index file to temp file /tmp/RtmpSKh2Ug/file718d18b041d

17:05:22 Searching Annoy index using 32 threads, search_k = 3000

17:05:23 Annoy recall = 100%

17:05:23 Commencing smooth kNN distance calibration using 32 threads
 with target n_neighbors = 30

17:05:24 Initializing from normalized Laplacian + noise (using irlba)

17:05:24 Commencing optimization for 500 epochs, with 45318 positive edges

17:05:26 Optimization finished

17:05:26 Creating temp model dir /tmp/RtmpSKh

In [7]:
MuSC_projAging1 <- addHarmony(
    ArchRProj = MuSC_projAging1,
    reducedDims = "IterativeLSI",
    name = "Harmony",
    groupBy = "Sample",
    force = TRUE
)

Filtering 1 dims correlated > 0.75 to log10(depth + 1)

Harmony 1/10

Harmony 2/10

Harmony 3/10

Harmony converged after 3 iterations



In [8]:
MuSC_projAging1 <- addUMAP(
    ArchRProj = MuSC_projAging1, 
    reducedDims = "Harmony", 
    name = "UMAP_Harmony", 
    nNeighbors = 30, 
    minDist = 0.5, 
    metric = "cosine",
    force = TRUE
)

17:05:27 UMAP embedding parameters a = 0.583 b = 1.334

17:05:27 Read 997 rows and found 29 numeric columns

17:05:27 Using Annoy for neighbor search, n_neighbors = 30

17:05:27 Building Annoy index with metric = cosine, n_trees = 50

0%   10   20   30   40   50   60   70   80   90   100%

[----|----|----|----|----|----|----|----|----|----|

*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
*
|

17:05:27 Writing NN index file to temp file /tmp/RtmpSKh2Ug/file718d4c90daae

17:05:27 Searching Annoy index using 32 threads, search_k = 3000

17:05:27 Annoy recall = 100%

17:05:28 Commencing smooth kNN distance calibration using 32 threads
 with target n_neighbors = 30

17:05:29 Initializing from normalized Laplacian + noise (using irlba)

17:05:29 Commencing optimization for 500 epochs, with 45582 positive edges

17:05:31 Optimization finished

17:05:31 Creating temp model dir /tmp/RtmpSKh2Ug/dir718d23e90b65

17:05:31 Creating dir /tmp/RtmpSKh

In [9]:
p1 <- plotEmbedding(ArchRProj = MuSC_projAging1, colorBy = "cellColData", name = "Age", embedding = "UMAP", size = 1, pal = c(Young = ggsci::pal_nejm()(2)[2], Aged = ggsci::pal_nejm()(2)[1]))
p2 <- plotEmbedding(ArchRProj = MuSC_projAging1, colorBy = "cellColData", name = "Age", embedding = "UMAP_Harmony", size = 1, pal = c(Young = ggsci::pal_nejm()(2)[2], Aged = ggsci::pal_nejm()(2)[1]))

plotPDF(p1, p2, name = "Plot-MuSC-Reclustered-Age.pdf", ArchRProj = MuSC_projAging1, addDOC = FALSE, width = 5, height = 5)

ArchR logging to : ArchRLogs/ArchR-plotEmbedding-718d46e910f0-Date-2022-12-23_Time-17-05-32.log
If there is an issue, please report to github with logFile!

Getting UMAP Embedding

ColorBy = cellColData

Plotting Embedding

1 


ArchR logging successful to : ArchRLogs/ArchR-plotEmbedding-718d46e910f0-Date-2022-12-23_Time-17-05-32.log

ArchR logging to : ArchRLogs/ArchR-plotEmbedding-718d48d50e34-Date-2022-12-23_Time-17-05-33.log
If there is an issue, please report to github with logFile!

Getting UMAP Embedding

ColorBy = cellColData

Plotting Embedding

1 


ArchR logging successful to : ArchRLogs/ArchR-plotEmbedding-718d48d50e34-Date-2022-12-23_Time-17-05-33.log

Plotting Ggplot!

Plotting Ggplot!



# MuSC QC metrics plots

In [10]:
MuSC_TSS <- plotTSSEnrichment(MuSC_projAging1, groupBy="Age", pal=ggsci::pal_nejm()(2))

ArchR logging to : ArchRLogs/ArchR-plotTSSEnrichment-718d75eb3d69-Date-2022-12-23_Time-17-07-29.log
If there is an issue, please report to github with logFile!

ArchR logging successful to : ArchRLogs/ArchR-plotTSSEnrichment-718d75eb3d69-Date-2022-12-23_Time-17-07-29.log



In [12]:
MuSC_fraghist <- plotFragmentSizes(MuSC_projAging1, groupBy="Age", pal=ggsci::pal_nejm()(2))

ArchR logging to : ArchRLogs/ArchR-plotFragmentSizes-718d598d3e55-Date-2022-12-23_Time-17-09-48.log
If there is an issue, please report to github with logFile!

ArchR logging successful to : ArchRLogs/ArchR-plotFragmentSizes-718d598d3e55-Date-2022-12-23_Time-17-09-48.log



In [14]:
plotPDF(list(MuSC_TSS, MuSC_fraghist), 
        name = "Plot-MuSC-TSS-FragHist-QCPlots.pdf", 
        ArchRProj = MuSC_projAging1, 
        addDOC = FALSE, width = 4, height = 4)

Plotting Ggplot!

Plotting Ggplot!



# Add MuSC peaks

In [15]:
MuSC_projAging1 <- addGroupCoverages(MuSC_projAging1, groupBy="Age", minCells = 50, maxCells=500, minReplicates = 3, maxReplicates=6, force = T)

ArchR logging to : ArchRLogs/ArchR-addGroupCoverages-718d21216eba-Date-2022-12-23_Time-17-18-56.log
If there is an issue, please report to github with logFile!

Aged (1 of 2) : CellGroups N = 3

Young (2 of 2) : CellGroups N = 3

2022-12-23 17:18:58 : Creating Coverage Files!, 0.034 mins elapsed.

2022-12-23 17:18:58 : Batch Execution w/ safelapply!, 0.034 mins elapsed.

2022-12-23 17:19:59 : Adding Kmer Bias to Coverage Files!, 1.049 mins elapsed.

Completed Kmer Bias Calculation

Adding Kmer Bias (1 of 6)

Adding Kmer Bias (2 of 6)

Adding Kmer Bias (3 of 6)

Adding Kmer Bias (4 of 6)

Adding Kmer Bias (5 of 6)

Adding Kmer Bias (6 of 6)

2022-12-23 17:20:19 : Finished Creation of Coverage Files!, 1.385 mins elapsed.

ArchR logging successful to : ArchRLogs/ArchR-addGroupCoverages-718d21216eba-Date-2022-12-23_Time-17-18-56.log



In [16]:
pathToMacs2 <- findMacs2()

Searching For MACS2..

Found with $path!



In [17]:
MuSC_projAging1 <- addReproduciblePeakSet(
    ArchRProj = MuSC_projAging1, 
    groupBy = "Age", 
    pathToMacs2 = pathToMacs2
)

ArchR logging to : ArchRLogs/ArchR-addReproduciblePeakSet-718d36707b24-Date-2022-12-23_Time-17-20-20.log
If there is an issue, please report to github with logFile!

Calling Peaks with Macs2

2022-12-23 17:20:20 : Peak Calling Parameters!, 0.008 mins elapsed.



      Group nCells nCellsUsed nReplicates nMin nMax maxPeaks
Aged   Aged    457        457           3   50  237   150000
Young Young    540        540           3   50  268   150000


2022-12-23 17:20:20 : Batching Peak Calls!, 0.009 mins elapsed.

2022-12-23 17:20:20 : Batch Execution w/ safelapply!, 0 mins elapsed.

2022-12-23 17:21:36 : Identifying Reproducible Peaks!, 1.267 mins elapsed.

2022-12-23 17:21:43 : Creating Union Peak Set!, 1.381 mins elapsed.

Converged after 3 iterations!

Plotting Ggplot!

2022-12-23 17:21:47 : Finished Creating Union Peak Set (54399)!, 1.46 mins elapsed.



In [24]:
MuSC_projAging1 <- addPeakMatrix(MuSC_projAging1)

ArchR logging to : ArchRLogs/ArchR-addPeakMatrix-718d6cede0c7-Date-2022-12-23_Time-17-25-35.log
If there is an issue, please report to github with logFile!

2022-12-23 17:25:35 : Batch Execution w/ safelapply!, 0 mins elapsed.

Overriding previous entry for ReadsInPeaks

Overriding previous entry for FRIP

ArchR logging successful to : ArchRLogs/ArchR-addPeakMatrix-718d6cede0c7-Date-2022-12-23_Time-17-25-35.log



# MuSC QC metrics

In [21]:
df <- getCellColData(MuSC_projAging1, select = c("Age","nFrags","TSSEnrichment","BlacklistRatio","FRIP"))

In [20]:
table(df$Age)


 Aged Young 
  457   540 

In [22]:
df %>% 
    as.data.frame() %>% 
    pivot_longer(!Age, names_to="metrics", values_to="value") %>% 
    group_by(Age, metrics) %>% 
    summarise(med = median(value)) %>% 
    pivot_wider(id_cols = Age, names_from = "metrics", values_from = "med")

`summarise()` has grouped output by 'Age'. You can override using the `.groups` argument.


Age   BlacklistRatio FRIP      nFrags  TSSEnrichment
1 Aged  0.02362131     0.3561413 10350.0 18.9530      
2 Young 0.02499256     0.5050324  3766.5 27.9435

In [25]:
peakmatrix <- getMatrixFromProject(MuSC_projAging1, "PeakMatrix")
young_cellnames <- rownames(colData(peakmatrix)[(colData(peakmatrix)$Age == "Young"),])
aged_cellnames <- rownames(colData(peakmatrix)[(colData(peakmatrix)$Age == "Aged"),])

summary(Matrix::colSums(assay(peakmatrix)[,young_cellnames] > 0))
summary(Matrix::colSums(assay(peakmatrix)[,aged_cellnames] > 0))

ArchR logging to : ArchRLogs/ArchR-getMatrixFromProject-718d47909817-Date-2022-12-23_Time-17-27-25.log
If there is an issue, please report to github with logFile!

2022-12-23 17:27:31 : Organizing colData, 0.1 mins elapsed.

2022-12-23 17:27:31 : Organizing rowData, 0.104 mins elapsed.

2022-12-23 17:27:31 : Organizing Assays (1 of 1), 0.105 mins elapsed.

2022-12-23 17:27:32 : Constructing SummarizedExperiment, 0.107 mins elapsed.

2022-12-23 17:27:34 : Finished Matrix Creation, 0.144 mins elapsed.



   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
    403    1178    1825    2169    2721   10373 

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
    377    1989    3685    4601    6560   16476 

# Peak2Gene Linkages

## Calculate P2G linkages

In [27]:
getAvailableMatrices(MuSC_projAging1)

[1] "GeneScoreMatrix"                     "Harmony_4iter_GeneIntegrationMatrix"
[3] "PeakMatrix"                          "TileMatrix"

In [28]:
MuSC_projAging1 <- addPeak2GeneLinks.mod(
    ArchRProj = MuSC_projAging1,
    reducedDims = "Harmony",
    useMatrix = "Harmony_4iter_GeneIntegrationMatrix",
    addEmpiricalPval = FALSE,
    maxDist = 5e5,
    group1 = grep("Young",getCellNames(MuSC_projAging1),fixed=TRUE,value=TRUE),
    group2 = grep("Aged",getCellNames(MuSC_projAging1),fixed=TRUE,value=TRUE)
)

ArchR logging to : ArchRLogs/ArchR-addPeak2GeneLinks-718d15a9ebcf-Date-2022-12-23_Time-17-31-10.log
If there is an issue, please report to github with logFile!

2022-12-23 17:31:11 : Getting Available Matrices, 0.005 mins elapsed.

2022-12-23 17:31:12 : Filtered Low Prediction Score Cells (0 of 997, 0), 0.004 mins elapsed.

Filtering 1 dims correlated > 0.75 to log10(depth + 1)

2022-12-23 17:31:12 : Computing KNN, 0.011 mins elapsed.

2022-12-23 17:31:13 : Identifying Non-Overlapping KNN pairs, 0.016 mins elapsed.

2022-12-23 17:31:14 : Identified 389 Groupings!, 0.047 mins elapsed.

Filtering 1 dims correlated > 0.75 to log10(depth + 1)

2022-12-23 17:31:14 : Computing KNN, 0.047 mins elapsed.

2022-12-23 17:31:15 : Identifying Non-Overlapping KNN pairs, 0.048 mins elapsed.

2022-12-23 17:31:16 : Identified 224 Groupings!, 0.071 mins elapsed.

2022-12-23 17:31:16 : Getting Group RNA Matrix, 0.072 mins elapsed.

2022-12-23 17:31:28 : Getting Group ATAC Matrix, 0.267 mins elapsed.

202

In [30]:
p2g <- getPeak2GeneLinks(MuSC_projAging1, returnLoops=FALSE)
saveRDS(p2g, file.path(projdir, 'MuSC_subset', 'all_MuSCs', 'all_MuSC_peak2gene.RDS'))

In [35]:
p2g_hmp_files <- plotPeak2GeneHeatmap(ArchRProj = MuSC_projAging1, groupBy = "Age", k=5, nPlot=dim(p2g)[1], returnMatrices = TRUE)

ArchR logging to : ArchRLogs/ArchR-plotPeak2GeneHeatmap-718d2ad5eeca-Date-2022-12-23_Time-17-39-32.log
If there is an issue, please report to github with logFile!

2022-12-23 17:39:37 : Determining KNN Groups!, 0.074 mins elapsed.

2022-12-23 17:39:43 : Ordering Peak2Gene Links!, 0.171 mins elapsed.



saveRDS(p2g_hmp_files, file.path(projdir, 'MuSC_subset', 'all_MuSCs', 'all_MuSC_peak2gene_clustered.RDS'))

In [49]:
p2g_hmp_files$ATAC

List of length 3
names(3): matrix kmeansId colData

## P2G heatmap

In [33]:
p2g_hmp <- plotPeak2GeneHeatmap(MuSC_projAging1, palGroup = c("Young"=ggsci::pal_nejm()(2)[2], "Aged"=ggsci::pal_nejm()(2)[1]), groupBy = "Age", k=5, nPlot=dim(p2g)[1], returnMatrices = FALSE)

ArchR logging to : ArchRLogs/ArchR-plotPeak2GeneHeatmap-718d268917de-Date-2022-12-23_Time-17-33-41.log
If there is an issue, please report to github with logFile!

2022-12-23 17:33:47 : Determining KNN Groups!, 0.089 mins elapsed.

2022-12-23 17:33:51 : Ordering Peak2Gene Links!, 0.166 mins elapsed.

2022-12-23 17:34:07 : Constructing ATAC Heatmap!, 0.42 mins elapsed.

Adding Annotations..

Preparing Main Heatmap..

2022-12-23 17:34:09 : Constructing RNA Heatmap!, 0.455 mins elapsed.

Adding Annotations..

Preparing Main Heatmap..

ArchR logging successful to : ArchRLogs/ArchR-plotPeak2GeneHeatmap-718d268917de-Date-2022-12-23_Time-17-33-41.log



In [34]:
plotPDF(p2g_hmp, name = "Plots-Peak-2-Gene-MuSC-Age_custom.pdf", ArchRProj = MuSC_projAging1, addDOC = FALSE, width = 5, height = 7)

Plotting ComplexHeatmap!

No legend element is put in the last 2 rows under `nrow = 4`, maybe you
should set `by_row = FALSE`? Reset `nrow` to 2.

No legend element is put in the last 2 rows under `nrow = 4`, maybe you
should set `by_row = FALSE`? Reset `nrow` to 2.

No legend element is put in the last 2 rows under `nrow = 4`, maybe you
should set `by_row = FALSE`? Reset `nrow` to 2.



## Get genes per cluster

In [36]:
p2g_list <- lapply(unique(p2g_hmp_files$ATAC$kmeansId), function(x) rownames(p2g_hmp_files$ATAC$matrix)[which(p2g_hmp_files$ATAC$kmeansId==x)])
names(p2g_list) <- unique(p2g_hmp_files$ATAC$kmeansId)

### export genes per kmeans group for GO term enrichment analysis

In [38]:
getOutputDirectory(MuSC_projAging1)

[1] "/nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/output"

In [40]:
for(n in names(p2g_list)) {
    write.table(unique(p2g_hmp_files$Peak2GeneLinks[p2g_list[[n]], 'gene']), file.path(getOutputDirectory(MuSC_projAging1), "Peak2GeneLinks", paste0("all_MuSC_projAging1_p2g_c",n,".txt")), row.names=F, col.names=F, quote=F)
}

In [43]:
gene_cluster_list <- lapply(names(p2g_list), function(x) p2g_hmp_files$Peak2GeneLinks[p2g_list[[x]], 'gene'])
gene_cluster_df <- data.frame(gene = unlist(gene_cluster_list))
gene_cluster_df$Cluster <- rep(names(p2g_list), sapply(gene_cluster_list, length))
gene_cluster_df <- unique(gene_cluster_df)

In [44]:
gene_cluster_df

gene          Cluster
1     Mrpl15        2      
2     Lypla1        2      
3     Rgs20         2      
5     Adhfe1        2      
11    Mybl1         2      
12    Mcmdc2        2      
13    Tcf24         2      
14    Cspp1         2      
16    Tram1         2      
18    Lactb2        2      
19    4930444P10Rik 2      
22    Ube2w         2      
24    Paqr8         2      
27    Tmem14a       2      
29    Ogfrl1        2      
31    Fam135a       2      
32    Dst           2      
36    Hs6st1        2      
38    Uggt1         2      
43    Cnnm3         2      
51    Ankrd39       2      
53    Sema4c        2      
65    Tmem131       2      
67    Coa5          2      
68    Unc50         2      
70    Mitd1         2      
74    Mrpl30        2      
76    Pdcl3         2      
77    Rnf149        2      
79    Mrps9         2      
⋮     ⋮             ⋮      
65489 Abcd1         5      
65494 Arhgap4       5      
65495 Renbp         5      
65500 Emd           5      
65501 Dnase1l1      5      
65504 Ikbkg         5      
65506 G6pdx         5      
65507 Gm6880        5      
65508 Tab3          5      
65509 Msn           5      
65511 Slc7a3        5      
65512 Foxo4         5      
65514 Med12         5      
65517 Slc16a2       5      
65518 Drp2          5      
65519 Armcx3        5      
65520 Gprasp2       5      
65521 Morf4l2       5      
65522 BC065397      5      
65523 Slc25a53      5      
65524 Esx1          5      
65525 Apex2         5      
65526 Wnk3          5      
65527 Phf8          5      
65528 Sms           5      
65529 Eif1ax        5      
65531 Rbbp7         5      
65532 Syap1         5      
65533 Ctps2         5      
65534 Pir           5

In [ ]:
young_MuSC_cellnames = grep("Young",getCellNames(MuSC_projAging1),fixed=T,value=T)
aged_MuSC_cellnames = grep("Aged",getCellNames(MuSC_projAging1),fixed=T,value=T)

exp_mat = getMatrixFromProject(MuSC_projAging1)

get_avg_exp = function(pattern, exp_mat, young_MuSC_cellnames, aged_MuSC_cellnames) {
    pattern_idx = grep(pattern,rowData(exp_mat)$name,fixed=T)
    pattern_avg_exp = data.frame(Young = Matrix::rowMeans(assay(exp_mat)[pattern_idx,young_MuSC_cellnames]),
                                Aged = Matrix::rowMeans(assay(exp_mat)[pattern_idx,aged_MuSC_cellnames]),
                                Young_sem = rowSds(assay(exp_mat)[pattern_idx,young_MuSC_cellnames]) / sqrt(length(young_MuSC_cellnames)),
                                Aged_sem = rowSds(assay(exp_mat)[pattern_idx,aged_MuSC_cellnames]) / sqrt(length(aged_MuSC_cellnames)),
                                row.names = rowData(exp_mat)$name[pattern_idx])
    return(pattern_avg_exp)
}

# Save MuSC object

In [45]:
saveArchRProject(ArchRProj = MuSC_projAging1, outputDirectory = file.path(projdir,"Save-MuSC_projAging1-02"), load = FALSE)

Copying ArchRProject to new outputDirectory : /nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/Save-MuSC_projAging1-02

Copying Arrow Files...

Copying Arrow Files (1 of 4)

Copying Arrow Files (2 of 4)

Copying Arrow Files (3 of 4)

Copying Arrow Files (4 of 4)

Getting ImputeWeights

No imputeWeights found, returning NULL

Copying Other Files...

Copying Other Files (1 of 26): Aged

Copying Other Files (2 of 26): Aged_v2

Copying Other Files (3 of 26): celltype_markersGS.RDS

Copying Other Files (4 of 26): Embeddings

Copying Other Files (5 of 26): GroupCoverages

Copying Other Files (6 of 26): Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Files (7 of 26): Harmony_Age_Clusters_res0.3_cluster_markersGS.RDS

Copying Other Files (8 of 26): IterativeLSI

Copying Other Files (9 of 26): IterativeLSI_4iter

Copying Other Files (10 of 26): IterativeLSI_4iter_10kvar

Copying Other Files (11 of 26): New_Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Fi

# Export RNA expression and Gene Activity matrices

In [5]:
MuSC_projAging1 <- readRDS(file.path(projdir,"Save-MuSC_projAging1-02","Save-ArchR-Project.rds"))

In [6]:
getAvailableMatrices(MuSC_projAging1)

[1] "GeneScoreMatrix"                     "Harmony_4iter_GeneIntegrationMatrix"
[3] "PeakMatrix"                          "TileMatrix"

In [9]:
rna_int_mat <- getMatrixFromProject(MuSC_projAging1, useMatrix='Harmony_4iter_GeneIntegrationMatrix')

ArchR logging to : ArchRLogs/ArchR-getMatrixFromProject-1c327760dcb7-Date-2022-12-25_Time-00-43-32.log
If there is an issue, please report to github with logFile!

2022-12-25 00:43:43 : Organizing colData, 0.195 mins elapsed.

2022-12-25 00:43:44 : Organizing rowData, 0.199 mins elapsed.

2022-12-25 00:43:44 : Organizing Assays (1 of 1), 0.199 mins elapsed.

2022-12-25 00:43:44 : Constructing SummarizedExperiment, 0.207 mins elapsed.

2022-12-25 00:43:45 : Finished Matrix Creation, 0.228 mins elapsed.



In [10]:
gene_activity_mat <- getMatrixFromProject(MuSC_projAging1, useMatrix='GeneScoreMatrix')

ArchR logging to : ArchRLogs/ArchR-getMatrixFromProject-1c3259befa27-Date-2022-12-25_Time-00-43-54.log
If there is an issue, please report to github with logFile!

2022-12-25 00:44:02 : Organizing colData, 0.146 mins elapsed.

2022-12-25 00:44:03 : Organizing rowData, 0.151 mins elapsed.

2022-12-25 00:44:03 : Organizing Assays (1 of 1), 0.151 mins elapsed.

2022-12-25 00:44:03 : Constructing SummarizedExperiment, 0.156 mins elapsed.

2022-12-25 00:44:05 : Finished Matrix Creation, 0.181 mins elapsed.



In [12]:
saveRDS(rna_int_mat, file.path(projdir, 'MuSC_subset', 'all_MuSC_rna_expression.RDS'))
saveRDS(gene_activity_mat, file.path(projdir, 'MuSC_subset', 'all_MuSC_gene_activity.RDS'))

# Export individual MuSC for each age 

In [54]:
aged_MuSC_cellnames <- MuSC_projAging1$cellNames[MuSC_projAging1$Age=="Aged"]
young_MuSC_cellnames <- MuSC_projAging1$cellNames[MuSC_projAging1$Age=="Young"]

In [55]:
head(aged_MuSC_cellnames)

[1] "Aged_v2#CTAATCCGTTAAGGTT-1" "Aged_v2#GTGCTTCTCTTGCTAT-1"
[3] "Aged_v2#GTGATCAGTGTAACCA-1" "Aged_v2#TCCGGTTTCTTTGAGA-1"
[5] "Aged_v2#CGGCTCACATGAATAG-1" "Aged_v2#AGAAACTAGATAACCC-1"

In [56]:
young_MuSC_projAging1 <- subsetArchRProject(MuSC_projAging1, cells = young_MuSC_cellnames, outputDirectory = file.path(projdir,"MuSC_subset","young_MuSC"), dropCells = TRUE, force = TRUE)

Copying ArchRProject to new outputDirectory : /nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/MuSC_subset/young_MuSC

Copying Arrow Files...

Getting ImputeWeights

No imputeWeights found, returning NULL

Copying Other Files...

Copying Other Files (1 of 26): Aged

Copying Other Files (2 of 26): Aged_v2

Copying Other Files (3 of 26): celltype_markersGS.RDS

Copying Other Files (4 of 26): Embeddings

Copying Other Files (5 of 26): GroupCoverages

Copying Other Files (6 of 26): Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Files (7 of 26): Harmony_Age_Clusters_res0.3_cluster_markersGS.RDS

Copying Other Files (8 of 26): IterativeLSI

Copying Other Files (9 of 26): IterativeLSI_4iter

Copying Other Files (10 of 26): IterativeLSI_4iter_10kvar

Copying Other Files (11 of 26): New_Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Files (12 of 26): Peak2GeneLinks

Copying Other Files (13 of 26): PeakCalls

Copying Other Files (14 of 26): Plots

Copying

In [57]:
aged_MuSC_projAging1 <- subsetArchRProject(MuSC_projAging1, cells = aged_MuSC_cellnames, outputDirectory = file.path(projdir,"MuSC_subset","aged_MuSC"), dropCells = TRUE, force = TRUE)

Copying ArchRProject to new outputDirectory : /nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/MuSC_subset/aged_MuSC

Copying Arrow Files...

Getting ImputeWeights

No imputeWeights found, returning NULL

Copying Other Files...

Copying Other Files (1 of 26): Aged

Copying Other Files (2 of 26): Aged_v2

Copying Other Files (3 of 26): celltype_markersGS.RDS

Copying Other Files (4 of 26): Embeddings

Copying Other Files (5 of 26): GroupCoverages

Copying Other Files (6 of 26): Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Files (7 of 26): Harmony_Age_Clusters_res0.3_cluster_markersGS.RDS

Copying Other Files (8 of 26): IterativeLSI

Copying Other Files (9 of 26): IterativeLSI_4iter

Copying Other Files (10 of 26): IterativeLSI_4iter_10kvar

Copying Other Files (11 of 26): New_Harmony_4iter_Clusters_res0.2_cluster_markersGS.RDS

Copying Other Files (12 of 26): Peak2GeneLinks

Copying Other Files (13 of 26): PeakCalls

Copying Other Files (14 of 26): Plots

Copying 

# Export bigwig tracks

In [13]:
getGroupBW(
  ArchRProj = MuSC_projAging1,
  groupBy = "Age",
  normMethod = "ReadsInTSS",
  tileSize = 100,
  maxCells = 1000,
  ceiling = 4,
  verbose = TRUE)

ArchR logging to : ArchRLogs/ArchR-getGroupBW-1c322d00b22a-Date-2022-12-25_Time-03-10-33.log
If there is an issue, please report to github with logFile!

2022-12-25 03:10:51 : Aged (1 of 2) : Creating BigWig for Group, 0.315 mins elapsed.

2022-12-25 03:11:02 : Young (2 of 2) : Creating BigWig for Group, 0.492 mins elapsed.

ArchR logging successful to : ArchRLogs/ArchR-getGroupBW-1c322d00b22a-Date-2022-12-25_Time-03-10-33.log



[1] "/nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/output/GroupBigWigs/Age/Aged-TileSize-100-normMethod-ReadsInTSS-ArchR.bw" 
[2] "/nas/homes/benyang/HiC/13_MultiOme/ArchR_analysis/output/GroupBigWigs/Age/Young-TileSize-100-normMethod-ReadsInTSS-ArchR.bw"

# Export peak-to-gene linkage object for plotgardener

In [65]:
p2g <- getPeak2GeneLinks(MuSC_projAging1, corCutOff=0.45, resolution=1, returnLoops=T)[[1]]
# young_MuSC_links = getPeak2GeneLinks(young_MuSC_projAging1, corCutOff=0, resolution=1, returnLoops=T)[[1]]
# aged_MuSC_links = getPeak2GeneLinks(aged_MuSC_projAging1, corCutOff=0, resolution=1, returnLoops=T)[[1]]

In [69]:
getPeak2GeneLinks(MuSC_projAging1, corCutOff=0.45, resolution=1, returnLoops=T)$Peak2GeneLinks

GRanges object with 65507 ranges and 2 metadata columns:
          seqnames              ranges strand |     value         FDR
             <Rle>           <IRanges>  <Rle> | <numeric>   <numeric>
      [1]     chr1     4785692-5070285      * |  0.643624 9.84521e-72
      [2]     chr1     4785726-4858619      * |  0.454769 5.88061e-32
      [3]     chr1     4807893-4858619      * |  0.541045 5.18773e-47
      [4]     chr1     4858619-5070285      * |  0.571748 1.65559e-53
      [5]     chr1    9545314-10038159      * |  0.483642 1.59373e-36
      ...      ...                 ...    ... .       ...         ...
  [65503]     chrX 166344767-166479867      * |  0.546261 4.54985e-48
  [65504]     chrX 167049461-167382749      * |  0.491559 7.43999e-38
  [65505]     chrX 167209218-167382794      * |  0.495334 1.67862e-38
  [65506]     chrX 169320372-169320404      * |  0.482208 2.75128e-36
  [65507]     chrX 169320404-169685199      * |  0.559641 7.26561e-51
  -------
  seqinfo: 20 sequences

In [67]:
p2g_genes <- getPeak2GeneLinks(MuSC_projAging1, corCutOff=0.45, resolution=1, returnLoops=F)
p2g_genes

DataFrame with 65536 rows and 6 columns
        idxATAC    idxRNA Correlation         FDR  VarQATAC   VarQRNA
      <integer> <integer>   <numeric>   <numeric> <numeric> <numeric>
1             7         4    0.454769 5.88061e-32  0.293608  0.922860
2             7         5    0.541045 5.18773e-47  0.293608  0.893475
3             4         7    0.643624 9.84521e-72  0.896414  0.598969
4             7         7    0.571748 1.65559e-53  0.293608  0.598969
5            25        16    0.464745 1.73906e-33  0.836118  0.990264
...         ...       ...         ...         ...       ...       ...
65532     54371     22683    0.546261 4.54985e-48  0.455909  0.797921
65533     54386     22688    0.495334 1.67862e-38  0.757367  0.926208
65534     54381     22691    0.491559 7.43999e-38  0.402324  0.552227
65535     54394     22696    0.482208 2.75128e-36  0.898969  0.887572
65536     54394     22697    0.559641 7.26561e-51  0.898969  0.778316

In [60]:
length(metadata(p2g_genes)$geneSet$name[p2g_genes$idxRNA])

[1] 185401

In [56]:
p2g$genes <- metadata(p2g_genes)$geneSet$name[p2g_genes$idxRNA]

ERROR: Error in `[[<-`(`*tmp*`, name, value = structure(c("Mrpl15", "Mrpl15", : 185401 elements in value to replace 185251 elements


In [19]:
## Convert LinkPeaks to bedpe files 
p2g_bedpe <- p2g_to_bedpe(p2g)

In [49]:
getPeak2GeneLinks(MuSC_projAging1, corCutOff=0, resolution=1, returnLoops=F)

DataFrame with 185401 rows and 6 columns
         idxATAC    idxRNA Correlation         FDR  VarQATAC   VarQRNA
       <integer> <integer>   <numeric>   <numeric> <numeric> <numeric>
1              3         4    0.201216 8.35049e-07  0.343462  0.922860
2              4         4    0.319359 1.30766e-15  0.896414  0.922860
3              5         4    0.376379 1.43176e-21  0.787919  0.922860
4              7         4    0.454769 5.88061e-32  0.293608  0.922860
5              3         5    0.299624 8.01191e-14  0.343462  0.893475
...          ...       ...         ...         ...       ...       ...
185397     54388     22694    0.166582 5.04817e-05  0.841082  0.786334
185398     54392     22696    0.213239 1.67152e-07  0.530800  0.887572
185399     54394     22696    0.482208 2.75128e-36  0.898969  0.887572
185400     54393     22697    0.203789 5.96661e-07  0.562970  0.778316
185401     54394     22697    0.559641 7.26561e-51  0.898969  0.778316

In [27]:
p2g_bedpe$bedpe_GI

GenomicInteractions object with 185251 interactions and 1 metadata column:
           seqnames1             ranges1     seqnames2             ranges2 |
               <Rle>           <IRanges>         <Rle>           <IRanges> |
       [1]      chr1     4571893-4571894 ---      chr1     4785726-4785727 |
       [2]      chr1     4571893-4571894 ---      chr1     4807893-4807894 |
       [3]      chr1     4785692-4785693 ---      chr1     4785726-4785727 |
       [4]      chr1     4785692-4785693 ---      chr1     4807893-4807894 |
       [5]      chr1     4785692-4785693 ---      chr1     5070285-5070286 |
       ...       ...                 ... ...       ...                 ... .
  [185247]      chrX 168673941-168673942 ---      chrX 168795099-168795100 |
  [185248]      chrX 169112967-169112968 ---      chrX 169320372-169320373 |
  [185249]      chrX 169302769-169302770 ---      chrX 169685199-169685200 |
  [185250]      chrX 169320372-169320373 ---      chrX 169320404-169320405 |
 

In [28]:
saveRDS(p2g_bedpe, file.path(projdir, 'output', 'Peak2GeneLinks', 'all_MuSC_p2g_bedpe.RDS'))